## Marine Data Literacy Course - Practical 1 <br> Model and Satellite CMEMS Sea Surface Temperature data <br> <font size="3">Adam Gauci</font>

**Contents**:

- Introduction
    - Targets of the practical
    - Datasets used in the practical
<br><br>
- Initialising the Python Environment
<br><br>
- Processing model data
    - Reading the model netcdf file
    - Processing single frames
    - Processing frames across time
    - Processing frames across depth
    - Extracting time series from model data
    - Extracting depth profile from model data
<br><br>
- Processing satellite data
    - Reading satellite netcdf file.
<br><br>
- Comparing Satellite and Model Data

***

### Introduction

This instruction sheet is meant to describe and list the structured activities, instructions and expected outputs for the practical exercise. It also serves to support the students to follow and execute the various steps of the exercise.

It is suggested that these instructions are kept open and available during the practical session such that instructions and pieces of code can be used directly without rewriting. 

The students will be asked to answer four MC questions which are based on outputs from the practical session. The tutors delivering the practical will guide you to prepare your answers at the appropriate stages of your practical, so that you will then submit your answers at the end of the session. 

#### Targets of the practical

The Copernicus Marine Environment Monitoring Service (CMEMS) is an EU information service based on satellite earth observations and in‑situ data. CMEMS provides state‑of‑the‑art analyses and forecasts of oceanographic parameters which offer an unprecedented capability to observe, understand, and anticipate marine environment events. CMEMS offers unique access to oceanographic products through an online catalogue. In this practical the students will learn how to:

- Log in the Marine Copernicus Portal.
- Download daily averaged sea surface temperature (SST) data from a Mediterranean  operational model that is available for ten consecutive forecast days.
- Download satellite observed SST data (L4) generated over the same domain and ten‑day period. Load and visualise the model and satellite netcdf files in Panoply.
- Visualise how model sea temperature varies with depth and time.
- Identify a grid cell in the model and satellite datasets, and extract the SST time series over the ten days being considered. 
- Regrid raster data to be able to compare two datasets.
- Generate a scatter plot to visualize the correlation between the model and the satellite. Compute the Mean Square Error between the model and satellite SST.

#### Datasets used in the practical

In this practical, files from the 'Mediterranean Sea High Resolution and Ultra High Resolution Sea Surface Temperature Analysis' model as well as from the 'Mediterranean Sea High Resolution and Ultra High Resolution Sea Surface Temperature Analysis' satellite datasets, will be used. Both products are downloadable from the Marine Copernicus Portal (CMEMS). 

*Mediterranean Sea High Resolution and Ultra High Resolution Sea Surface Temperature Analysis*

The physical component of the Mediterranean Forecasting System (Med-Currents) is a coupled hydrodynamic-wave model implemented over the whole Mediterranean Basin including tides. The model horizontal grid resolution is 1/24˚ (ca. 4 km) and has 141 unevenly spaced vertical levels. The hydrodynamics are supplied by the Nucleous for European Modelling of the Ocean (NEMO v3.6) while the wave component is provided by Wave Watch-III; the model solutions are corrected by a variational data assimilation scheme (3DVAR) of temperature and salinity vertical profiles and along track satellite Sea Level Anomaly observations.

Filename: `med-cmcc-tem-an-fc-h_1634968902280.nc` <br>
Product type: `Forecast` <br>
Spatial resolution: `0.042° × 0.042°` <br>
Vertical coverage: `from 1.01824 down to 1005.14 (74 levels)` <br>
Time period: `20/10/2021 00:30 to 22/10/2021 23:30 (72 time steps)` <br>

 *Mediterranean Sea High Resolution and Ultra High Resolution Sea Surface Temperature Analysis*

For the Mediterranean Sea (MED), the CNR MED Sea Surface Temperature (SST) processing chain provides daily gap-free (L4) maps at high (HR 0.0625°) and ultra-high (UHR 0.01°) spatial resolution over the Mediterranean Sea. Remotely-sensed L4 SST datasets are operationally produced and distributed in near-real time by the Consiglio Nazionale delle Ricerche - Gruppo di Oceanografia da Satellite (CNR-GOS). These SST products are based on the nighttime images collected by the infrared sensors mounted on different satellite platforms, and cover the Southern European Seas. The CNR-GOS processing chain includes several modules, from the data extraction and preliminary quality control, to cloudy pixel removal and satellite images collating/merging. A two-step algorithm finally allows to interpolate SST data at high (HR 0.0625°) and ultra-high (UHR 0.01°) spatial resolution, applying statistical techniques. These L4 data are also used to estimate the SST anomaly with respect to a pentad climatology. 

Filename: `SST_MED_SST_L4_NRT_OBSERVATIONS_010_004_c_V2_1634969733519.nc` <br>
Product type: `Satellite (L4)` <br>
Spatial resolution: `0.042° × 0.042°` <br>
Vertical coverage: `surface (1 level)` <br>
Time period: `20/10/2021 00:00 to 22/10/2021 23:00 (3 time steps)` <br>


***

### Initialising the Python Environment

Downloading model and satellite data files. These were originally obtained from CMEMS.

In [ ]:
!wget http://ioi.research.um.edu.mt/staff/adam/download/SEAEU/SST_MED_SST_L4_NRT_OBSERVATIONS_010_004_c_V2_1634969733519.nc
!wget http://ioi.research.um.edu.mt/staff/adam/download/SEAEU/med-cmcc-tem-an-fc-h_1634968902280.nc

Importing the required libraries in Python.

In [2]:
import netCDF4 as nc
import matplotlib.pyplot as plt
import datetime
import time
import IPython.display as display
import scipy.interpolate as interp
import numpy as np

***

### Processing model data

#### Reading the model netcdf file

Defining the filename and importing the netcdf dataset.

In [3]:
modelFilename = 'med-cmcc-tem-an-fc-h_1634968902280.nc'
modelDataSet = nc.Dataset(modelFilename)

Printing the metadata of the netcdf file and of the 'thetao' and 'time' varibales to check dimensions, units, and see how these are defined.

In [ ]:
print(modelDataSet)

In [ ]:
print (modelDataSet['thetao'])

In [ ]:
print(modelDataSet['time'])

Reading the variables from the model nc file.

In [8]:
modelLon = modelDataSet['lon']
modelLat = modelDataSet['lat']
modelDepth = modelDataSet['depth']
modelTemperature = modelDataSet['thetao']
modelTime = modelDataSet['time']

#### Processing single frames

Extracting temperature values across all longitudes and all latitudes, for the first time frame (out of 72), and the first depth level (out of 74).

In [9]:
modelTemp1 = modelTemperature[0,0,:,:];

Calculating the time corresponding to this frame.

In [12]:
modelBaseDate =  datetime.datetime(1900, 1, 1, 0, 0, 0);

timeMins = float(modelTime[0])
modelTimeDT1 = modelBaseDate + datetime.timedelta(minutes = timeMins)

Plotting the extracted temperature data (modelTemp1).

In [ ]:
plt.pcolor(modelLon, modelLat, modelTemp1);
plt.ylabel("Latitude ($^\circ$N)");
plt.xlabel("Longitude ($^\circ$E)");
plt.title("Model Sea Temperature \non " +  modelTimeDT1.strftime("%d/%m/%y %H:%M") + "\nat depth " + "{:.2f}".format(modelDepth[0]) + "m");
plt.colorbar();

<font color=red>
Exercise 1 (replace ?? with the correct terms): <br>
- Extract temperature values across all longitudes and all latitudes, for the 24th time frame and the first depth level. <br>
- Calculate the time corresponding to this frame. <br>
- Plot the extracted temperature data (modelTemp2). <br>
</font>

In [ ]:
modelTemp2 = modelTemperature[??,0,:,:];

timeMins = float(modelTime[??])
modelTimeDT2 = modelBaseDate + datetime.timedelta(minutes = timeMins)

plt.pcolor(modelLon, modelLat, modelTemp2);
plt.ylabel("Latitude ($^\circ$N)");
plt.xlabel("Longitude ($^\circ$E)");
plt.title("Model Sea Temperature \non " +  modelTimeDT2.strftime("%d/%m/%y %H:%M") + "\nat depth " + "{:.2f}".format(modelDepth[0]) + "m");
plt.colorbar();

Compute and plot difference in tempeature between the two days.

In [ ]:
modelDiff = modelTemp2 - modelTemp1;

plt.pcolor(modelLon, modelLat, modelDiff);
plt.ylabel("Latitude ($^\circ$N)");
plt.xlabel("Longitude ($^\circ$E)");
plt.title("Model Sea Temperature Difference \nbetween " +  modelTimeDT1.strftime("%d/%m/%y %H:%M") + " and " + modelTimeDT2.strftime("%d/%m/%y %H:%M") + "\nat depth " + "{:.2f}".format(modelDepth[0]) + "m");
plt.colorbar();
plt.set_cmap('jet')

Generate a histogram of the residuals between -2 and 2, and use 50 bins.

In [ ]:
plt.hist(modelDiff.flatten(), np.linspace(-2,2,50));

<font color=blue>
Quiz Question 1: <br>
The majority of sea temperature values between the two days are: <br>
1. The same <br>
2. Colder in day 1 than in day 2 <br>
3. Colder in day 2 than in day 1 <br>
4. This histogram does not give this information <br>
</font>

#### Processing frames across time

Looping over all time frames (but showing every 5th frame).

In [ ]:
nTimeFrames = modelTemperature.shape[0];

for t in range(0, (nTimeFrames-1), 5):
    d = 0;
    
    timeMins = float(modelTime[t])
    modelTimeCurr = modelBaseDate + datetime.timedelta(minutes = timeMins)
    
    modelTemp = modelTemperature[t,d,:,:];

    plt.clf()
    plt.pcolor(modelLon, modelLat, modelTemp);
    plt.ylabel("Latitude ($^\circ$N)");
    plt.xlabel("Longitude ($^\circ$E)");
    plt.title("Model Sea Temperature \non " +  modelTimeCurr.strftime("%d/%m/%y %H:%M") + "\nat depth " + "{:.2f}".format(modelDepth[d]) + "m");
    plt.colorbar();
    plt.clim([19, 25]);
    display.display(plt.gcf())
    display.clear_output(wait=True)
    #time.sleep(0.25)

#### Processing frames across depth

Looping over all depth levels, for the first time frame, and showing the whole domain. 

In [ ]:
nDepthFrames = modelTemperature.shape[1];

for d in range(nDepthFrames):
    
    t = 0;
    timeMins = float(modelTime[t])
    modelTimeCurr = modelBaseDate + datetime.timedelta(minutes = timeMins)
    
    modelTemp = modelTemperature[t,d,:,:];

    plt.clf()
    plt.pcolor(modelLon, modelLat, modelTemp);
    plt.ylabel("Latitude ($^\circ$N)");
    plt.xlabel("Longitude ($^\circ$E)");
    plt.title("Model Sea Temperature \non " +  modelTimeCurr.strftime("%d/%m/%y %H:%M") + "\nat depth " + "{:.2f}".format(modelDepth[d]) + "m");
    plt.colorbar();
    #plt.clim([19, 25]);
    display.display(plt.gcf())
    display.clear_output(wait=True)
    #time.sleep(0.25)

<font color=red>
Exercise 2 (replace ?? with the correct terms): <br>
- Define the number of depth frames (nDepthFrames)<br>
- Identify the time frame corresponding to 20/12/21 12:30 (t) <br>
- Loop over all depth levels. <br>
</font>

In [ ]:
nDepthFrames = ??.shape[1];

for d in range(nDepthFrames):
    
    t = ??;
    timeMins = float(modelTime[t])
    modelTimeCurr = modelBaseDate + datetime.timedelta(minutes = timeMins)
    
    modelTemp = modelTemperature[t,d,:,:];

    plt.clf()
    plt.pcolor(modelLon, modelLat, modelTemp);
    plt.ylabel("Latitude ($^\circ$N)");
    plt.xlabel("Longitude ($^\circ$E)");
    plt.title("Model Sea Temperature \non " +  modelTimeCurr.strftime("%d/%m/%y %H:%M") + "\nat depth " + "{:.2f}".format(modelDepth[d]) + "m");
    plt.colorbar();
    display.display(plt.gcf())
    display.clear_output(wait=True)
    #time.sleep(0.25)

#### Extracting time series from model data

Defining required coordinates.

In [53]:
reqLon = 16.0;
modelLonIdx = 144

reqLat = 36.0;
modelLatIdx = 71

Showing Point on map.

In [ ]:
modelTemp = modelTemperature[0,0,:,:];
plt.pcolor(modelLon, modelLat, modelTemp);
plt.plot(modelLon[modelLonIdx], modelLat[modelLatIdx], 'ko')
plt.ylabel("Latitude ($^\circ$N)");
plt.xlabel("Longitude ($^\circ$E)");
plt.title("Model Sea Temperature \non " +  modelTimeCurr.strftime("%d/%m/%y %H:%M") + "\nat depth " + "{:.2f}".format(modelDepth[d]) + "m");
plt.colorbar();
plt.clim([18, 26]);

Extracting and plotting time series.

In [ ]:
depthLevel = 0;

modelTimeSeries = modelTemperature[:,depthLevel,modelLatIdx,modelLonIdx];

plt.plot(modelTimeSeries);
plt.ylabel("Temperature ($^\circ$C)");
plt.xlabel("Time");
plt.title("Time Series \nLon: " + "{:.3f}".format(modelLon[modelLonIdx]) + "$^\circ$E, Lat: " + "{:.3f}".format(modelLat[modelLatIdx])+ "$^\circ$N \n Depth level: " + "{:.3f}".format(modelDepth[depthLevel])+ "m");
plt.autoscale(enable=True, axis='x', tight=True)


<font color=red>
Exercise 3 (replace ?? with the correct terms): <br>
- Compute the sea temperature predicted by the model for 21/10/2021 12:30, for the first depth level (1.018m) at 16.0 degE in longitude and 36.0 degN in latitude;
</font>

In [ ]:
depthLevel = ??;
timeFrame = ??;

timeMins = float(modelTime[timeFrame])
modelTimeCurr = modelBaseDate + datetime.timedelta(minutes = timeMins)

depthCurr = modelDepth[depthLevel];

modelTempValue = modelTemperature[timeFrame,depthLevel,??,??];
    
print("Model temperature at " + modelTimeCurr.strftime("%d/%m/%y %H:%M") + " at " + "{:.3f}".format(depthCurr) + "m is " + str(modelTempValue) + "deg C");

<font color=blue>
Quiz Question 2: <br>
What is the sea temperature predicted by the model for 21/10/2021 12:30 at the first depth level (1.018m) at 16.0 degE in longitude and 36.0 degN in latitude: <br>
1. 19.82 degC <br>
2. 20.13 degC <br>
3. 21.78 degC <br>
4. 22.07 degC <br>
</font>

#### Extracting depth profile from model data

Extracting and plotting depth profile.

In [ ]:
timeStep = 0;
timeMins = float(modelTime[timeStep]);
modelTimeStep = modelBaseDate + datetime.timedelta(minutes = timeMins);

modelDepthProfile = modelTemperature[timeStep,:,modelLatIdx,modelLonIdx];

plt.plot(modelDepthProfile, modelDepth);
plt.gca().invert_yaxis();
plt.ylabel("Depth (m)")
plt.xlabel("Temperature ($^\circ$C)")
plt.title("Depth Profile \nLon: " + "{:.3f}".format(modelLon[modelLonIdx]) + "$^\circ$E, Lat: " + "{:.3f}".format(modelLat[modelLatIdx])+ "$^\circ$N \n " + modelTimeStep.strftime("%d/%m/%y %H:%M"));

***

### Processing satellite data

#### Reading satellite netcdf file.

In [60]:
satFilename = 'SST_MED_SST_L4_NRT_OBSERVATIONS_010_004_c_V2_1634969733519.nc'
satDataSet = nc.Dataset(satFilename)

Printing metadata of the netcdf file and of other parameters.

In [ ]:
print(satDataSet)

In [ ]:
print (satDataSet['analysed_sst'])

In [ ]:
print (satDataSet['time'])

Reading the variables from the satellite nc file.

In [64]:
satLon = satDataSet['lon']
satLat = satDataSet['lat']
satTemperature = satDataSet['analysed_sst']
satTime = satDataSet['time']

Extracting temperature values across all longitudes and all latitudes, for the first time frame (out of 72), and converting values from Kelvin to Celcius.

In [65]:
satTemp1 = satTemperature[0,:,:];
satTemp1 -= 273.15;

Calculating the time corresponding to this frame.

In [66]:
satBaseDate =  datetime.datetime(1981, 1, 1, 0, 0, 0);

timeSecs = float(satTime[0])
satTimeDT1 = satBaseDate + datetime.timedelta(seconds = timeSecs)

Plotting the extracted satellite data (satTemp1).

In [ ]:
plt.pcolor(satLon, satLat, satTemp1);
plt.ylabel("Latitude ($^\circ$N)");
plt.xlabel("Longitude ($^\circ$E)");
plt.title("Satellite Sea Surface Temperature \non " +  satTimeDT1.strftime("%d/%m/%y %H:%M"));
plt.colorbar();

<font color=red>
Exercise 4 (replace ?? with the correct terms): <br>
- Extract satellite temperature values across all longitudes and all latitudes, for the second time frame <br>
- Convert temperature values from Kelvin to Celcius<br>
- Calculate the time corresponding to this frame <br>
- Plot the extracted temperature data (satTemp2)
</font>

In [ ]:
satTemp2 = satTemperature[??,??,??];
satTemp2 -= ??;

timeSecs = float(satTime[1])
satTimeDT2 = satBaseDate + datetime.timedelta(seconds = timeSecs)

plt.pcolor(satLon, satLat, ??);
plt.ylabel("Latitude ($^\circ$N)");
plt.xlabel("Longitude ($^\circ$E)");
plt.title("Satellite Sea Surface Temperature \non " +  satTimeDT2.strftime("%d/%m/%y %H:%M"));
plt.colorbar();

Compute and plot difference in temperature between the two days.

In [ ]:
satDiff = satTemp2 - satTemp1;

plt.pcolor(satLon, satLat, satDiff);
plt.ylabel("Latitude ($^\circ$N)");
plt.xlabel("Longitude ($^\circ$E)");
plt.title("Satellite Sea Surface Temperature Difference \nbetween " +  satTimeDT1.strftime("%d/%m/%y %H:%M") + " and " + satTimeDT2.strftime("%d/%m/%y %H:%M"));
plt.colorbar();
plt.set_cmap('jet')

Generate a histogram of the residuals between -2 and 2, and use 10 bins.

In [ ]:
plt.hist(satDiff.flatten(), np.linspace(-2,2,50));

<font color=blue>
Quiz Question 3: <br>
The majority of sea temperature values between the two days are: <br>
1. The same <br>
2. Colder in day 1 than in day 2 <br>
3. Colder in day 2 than in day 1 <br>
4. This histogram does not give this information <br>
</font>

### Comparing Satellite and Model Data

In [80]:
modelTemp = modelTemperature[0,0,:,:];

satTemp = satTemperature[0,:,:];
satTemp -= 273.15;

xi, yi = np.meshgrid(satLon, satLat)
Xi, Yi = np.meshgrid(modelLon, modelLat)

satTempInterp = interp.griddata((xi.flatten(), yi.flatten()), satTemp.flatten(), (Xi.flatten(), Yi.flatten()), method='linear')
satTempInterp = np.reshape(satTempInterp, Xi.shape)

In [ ]:
plt.pcolor(modelLon, modelLat, satTempInterp);
plt.clim([20, 25]);
plt.ylabel("Latitude ($^\circ$N)");
plt.xlabel("Longitude ($^\circ$E)");
plt.title("Satellite SST Interpolated on Model Grid");
plt.colorbar();

In [ ]:
tempDiff = modelTemp - satTempInterp
plt.pcolor(modelLon, modelLat, tempDiff);
plt.clim([-5, 5]);
plt.ylabel("Latitude ($^\circ$N)");
plt.xlabel("Longitude ($^\circ$E)");
plt.title("Model SST - Satellite SST");
plt.colorbar();

In [ ]:
x, y, z = plt.hist(tempDiff.flatten(), np.linspace(-2,2,50));
elem = np.argmax(x)
y[elem]

<font color=blue>
Quiz Question 4: <br>
What is the most common temperature difference between the model and satellite datasets for 20/10/2021 00:00: <br>
1. 0.07846 degC <br>
2. 0.12245 degC <br>
3. 0.15632 degC <br>
4. 0.18370 degC <br>
</font>